In [1]:
!pip install mlflow
from pyspark.ml import Pipeline
from pyspark.ml.regression import RandomForestRegressor
from pyspark.ml.feature import PCA, VectorAssembler
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder
from pyspark.ml.evaluation import RegressionEvaluator
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

In [2]:
#Load the feature table
train_df=spark.read.parquet('/FileStore/my-stuff/df_train_final.parquet')
display(train_df)

created_utc domain num_comments score subreddit idx index timestamp is_crosspostable_encoded domaintfidf total_subreddit_posts subreddit_hotness subreddit_author_count binned_score author_cakeday_encoded author_flair_text_color_encoded brand_safe_encoded no_follow_enc over_18_enc subreddit_rev create_hour DOW DOW_value created_hour_sin created_hour_cos length_title titlewordCount url_length has_exclamation_mark has_question_mark average_da resultIndex lastIndex protocolIndex result1Index subreddit_rev_Index DOW_Index whitelist_statusIndex subreddit_typeIndex result_ohe DOW_ohe subreddit_type_ohe total_author_score_ntile_ohe whitelist_status_ohe subreddit_rev_ohe avg_author_score_ntile_ohe result1_ohe last_ohe protocol_ohe 1141171234 macgeekery.com 0 0 reddit.com 0 1 2006-03-01T00:00:34.000+0000 1 List(0, 262144, List(22756), List(7.826123850651258)) 8503 1 1841 1 0 0 1 1 0 reddit.com 0 Wed 4 0.0 1.0 20 5 47 0 0 93.46056782334385 0.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 List(0, 2, List(0), List(1.0)) List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(8), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 13, List(0), List(1.0)) List(0, 10, List(7), List(1.0)) List(0, 3, List(0), List(1.0)) List(0, 23, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1141171723 msnbc.msn.com 0 0 reddit.com 1 2 2006-03-01T00:08:43.000+0000 1 List(0, 262144, List(8886, 148676), List(5.651372129167097, 5.308427378040267)) 8503 2 1841 1 0 0 1 1 0 reddit.com 0 Wed 4 0.0 1.0 94 18 44 0 0 93.46056782334385 1.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 List(0, 2, List(1), List(1.0)) List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(5), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 13, List(0), List(1.0)) List(0, 10, List(4), List(1.0)) List(0, 3, List(0), List(1.0)) List(0, 23, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1141171939 iht.com 0 0 reddit.com 2 3 2006-03-01T00:12:19.000+0000 1 List(0, 262144, List(118857), List(6.727511561983148)) 8503 3 1841 1 0 0 1 1 0 reddit.com 0 Wed 4 0.0 1.0 61 10 51 0 0 93.46056782334385 0.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 List(0, 2, List(0), List(1.0)) List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(7), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 13, List(0), List(1.0)) List(0, 10, List(5), List(1.0)) List(0, 3, List(0), List(1.0)) List(0, 23, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1141172277 faelle.com 0 0 reddit.com 4 5 2006-03-01T00:17:57.000+0000 1 List(0, 262144, List(251608), List(8.33694947441725)) 8503 5 1841 1 0 0 1 1 0 reddit.com 0 Wed 4 0.0 1.0 31 6 55 0 0 93.46056782334385 1.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 List(0, 2, List(1), List(1.0)) List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(9), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 13, List(0), List(1.0)) List(0, 10, List(9), List(1.0)) List(0, 3, List(0), List(1.0)) List(0, 23, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1141172696 request.reddit.com 1 0 reddit.com 5 6 2006-03-01T00:24:56.000+0000 1 List(0, 262144, List(13520, 38868), List(4.2206260054763725, 6.103357252910154)) 8503 6 1841 1 0 0 1 1 0 reddit.com 0 Wed 4 0.0 1.0 17 2 31 0 0 93.46056782334385 2.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 List(0, 2, List(), List()) List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(7), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 13, List(0), List(1.0)) List(0, 10, List(5), List(1.0)) List(0, 3, List(0), List(1.0)) List(0, 23, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1141173165 pandora.com 0 4 pl 6 7 2006-03-01T00:32:45.000+0000 0 List(0, 262144, List(55603), List(8.049267401965468)) 35 1 11 1 0 0 0 1 0 pl 0 Wed 4 0.0 1.0 61 12 12 0 0 93.46056782334385 0.0 0.0 0.0 0.0 11.0 1.0 1.0 2.0 List(0, 2, List(0), List(1.0)) List(0, 6, List(1), List(1.0)) List(0, 2, List(), List()) List(0, 10, List(8), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 13, List(11), List(1.0)) List(0, 10, List(7), List(1.0)) 

In [3]:
#Drop Redundant features
#train_df=train_df.drop('created_utc','domain','subreddit','idx','index','timestamp','subreddit_rev','DOW','DOW_value','whitelist_statusIndex','whitelist_status_ohe','binned_score','DOW_Index','resultIndex','lastIndex','protocolIndex','result1Index','subreddit_rev_Index','subreddit_typeIndex','domaintfidf')
train_df=train_df.drop('created_utc','domain','subreddit','idx','index','timestamp','subreddit_rev','DOW','DOW_value','whitelist_statusIndex','whitelist_status_ohe','binned_score','DOW_Index','resultIndex','lastIndex','protocolIndex','result1Index','subreddit_rev_Index','subreddit_typeIndex','domaintfidf','total_author_score_ntile_ohe','subreddit_author_count','total_subreddit_posts','titlewordCount','avg_author_score_ntile_ohe','result_ohe','subreddit_rev_ohe','last_ohe','protocol_ohe','created_hour')
display(train_df)

num_comments score is_crosspostable_encoded subreddit_hotness author_cakeday_encoded author_flair_text_color_encoded brand_safe_encoded no_follow_enc over_18_enc create_hour created_hour_sin created_hour_cos length_title url_length has_exclamation_mark has_question_mark average_da DOW_ohe subreddit_type_ohe result1_ohe 0 0 1 1 0 0 1 1 0 0 0.0 1.0 20 47 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 2 0 0 1 1 0 0 0.0 1.0 94 44 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 3 0 0 1 1 0 0 0.0 1.0 61 51 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 5 0 0 1 1 0 0 0.0 1.0 31 55 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 0 1 6 0 0 1 1 0 0 0.0 1.0 17 31 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 4 0 1 0 0 0 1 0 0 0.0 1.0 61 12 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(), List()) List(0, 3, List(0), List(1.0)) 0 0 1 7 0 0 1 1 0 0 0.0 1.0 34 58 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 7 1 1 0 0 1 1 0 0 0.0 1.0 32 69 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 1 9 1 8 0 0 1 0 0 0 0.0 1.0 29 64 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 2 39 1 9 0 0 1 0 0 0 0.0 1.0 71 67 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 1 10 0 0 1 0 0 0 0.0 1.0 46 86 0 1 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 0 0 11 0 0 1 1 0 1 0.26979676 0.96291727 39 41 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 12 0 0 1 1 0 1 0.26979676 0.96291727 21 62 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 0 0 13 0 0 1 1 0 1 0.26979676 0.96291727 42 40 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 14 0 0 1 1 0 1 0.26979676 0.96291727 40 78 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 12 1 15 0 0 1 0 0 1 0.26979676 0.96291727 38 61 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 19 0 5 0 0 0 1 0 1 0.26979676 0.96291727 27 43 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 1 0 0 18 0 1 1 1 0 1 0.26979676 0.96291727 73 33 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 0 0 19 0 0 1 1 0 1 0.26979676 0.96291727 16 52 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 1 1 20 0 0 1 1 0 1 0.26979676 0.96291727 81 46 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 0 1 1 0 0 0 1 0 2 0.51958394 0.8544194 48 32 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 4 8 1 22 0 0 1 0 0 2 0.51958394 0.8544194 24 89 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 5 0 1 2 0 0 0 1 0 2 0.51958394 0.8544194 51 32 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 1 0 1 23 0 0 1 1 0 2 0.51958394 0.8544194 13 81 0 0 93.46056782334385 List(0, 

In [4]:
display(train_df.describe())

summary num_comments score is_crosspostable_encoded subreddit_hotness author_cakeday_encoded author_flair_text_color_encoded brand_safe_encoded no_follow_enc over_18_enc create_hour created_hour_sin created_hour_cos length_title url_length has_exclamation_mark has_question_mark average_da count 12190 12190 12190 12190 12190 12190 12190 12190 12190 12190 12190 12190 12190 12190 12190 12190 12190 mean 1.061853978671042 7.636177194421657 0.8797374897456932 1207.2121410992618 0.008859721082854799 0.06694011484823625 0.7895816242821985 0.7904019688269073 0.04790812141099262 12.405988515176373 -0.11508347067166001 -0.004288369198379407 43.8188679245283 52.03937653814602 0.030352748154224774 0.04881050041017227 93.42417244966757 stddev 5.2096057401856015 29.39500651296162 0.3252815992228017 811.6201445991428 0.09371204216859019 0.24992850996603388 0.40762251336770405 0.4070384355235982 0.21358060645327295 6.604367390022807 0.7088114621060027 0.6959918501764683 22.0978069978482 23.59006546655168 0.17156303047411006 0.21548049672977812 0.23073301013173603 min 0 0 0 1 0 0 0 0 0 0 -0.99766874 -0.99068594 1 7 0 0 92.0 max 225 583 1 2042 1 1 1 1 1 23 0.99766874 1.0 361 307 1 1 97.0

In [5]:
X_train=train_df.drop('score')
display(X_train)

num_comments is_crosspostable_encoded subreddit_hotness author_cakeday_encoded author_flair_text_color_encoded brand_safe_encoded no_follow_enc over_18_enc create_hour created_hour_sin created_hour_cos length_title url_length has_exclamation_mark has_question_mark average_da DOW_ohe subreddit_type_ohe result1_ohe 0 1 1 0 0 1 1 0 0 0.0 1.0 20 47 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 2 0 0 1 1 0 0 0.0 1.0 94 44 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 3 0 0 1 1 0 0 0.0 1.0 61 51 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 5 0 0 1 1 0 0 0.0 1.0 31 55 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 1 6 0 0 1 1 0 0 0.0 1.0 17 31 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 0 0 0 1 0 0 0.0 1.0 61 12 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(), List()) List(0, 3, List(0), List(1.0)) 0 1 7 0 0 1 1 0 0 0.0 1.0 34 58 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 1 0 0 1 1 0 0 0.0 1.0 32 69 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 1 1 8 0 0 1 0 0 0 0.0 1.0 29 64 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 2 1 9 0 0 1 0 0 0 0.0 1.0 71 67 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 10 0 0 1 0 0 0 0.0 1.0 46 86 0 1 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 0 11 0 0 1 1 0 1 0.26979676 0.96291727 39 41 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 12 0 0 1 1 0 1 0.26979676 0.96291727 21 62 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 0 13 0 0 1 1 0 1 0.26979676 0.96291727 42 40 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 14 0 0 1 1 0 1 0.26979676 0.96291727 40 78 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 15 0 0 1 0 0 1 0.26979676 0.96291727 38 61 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 5 0 0 0 1 0 1 0.26979676 0.96291727 27 43 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 1 0 18 0 1 1 1 0 1 0.26979676 0.96291727 73 33 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 0 19 0 0 1 1 0 1 0.26979676 0.96291727 16 52 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 1 20 0 0 1 1 0 1 0.26979676 0.96291727 81 46 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 1 1 0 0 0 1 0 2 0.51958394 0.8544194 48 32 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 4 1 22 0 0 1 0 0 2 0.51958394 0.8544194 24 89 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 5 1 2 0 0 0 1 0 2 0.51958394 0.8544194 51 32 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 1 1 23 0 0 1 1 0 2 0.51958394 0.8544194 13 81 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) Lis

In [6]:
 print(len(X_train.columns))

19

In [7]:
vect_asmb=VectorAssembler(inputCols=X_train.columns,outputCol='features')
training_df=vect_asmb.transform(train_df).select('features','score')
display(training_df)

features score List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 17, 22, 24), List(1.0, 1.0, 1.0, 1.0, 1.0, 20.0, 47.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 17, 22, 24), List(1.0, 2.0, 1.0, 1.0, 1.0, 94.0, 44.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 17, 22, 24), List(1.0, 3.0, 1.0, 1.0, 1.0, 61.0, 51.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 17, 22, 24), List(1.0, 5.0, 1.0, 1.0, 1.0, 31.0, 55.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 1, 2, 5, 6, 10, 11, 12, 15, 17, 22, 24), List(1.0, 1.0, 6.0, 1.0, 1.0, 1.0, 17.0, 31.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(2, 6, 10, 11, 12, 15, 17, 24), List(1.0, 1.0, 1.0, 61.0, 12.0, 93.46056782334385, 1.0, 1.0)) 4 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 17, 22, 24), List(1.0, 7.0, 1.0, 1.0, 1.0, 34.0, 58.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 17, 23, 24), List(1.0, 1.0, 1.0, 1.0, 1.0, 32.0, 69.0, 93.46056782334385, 1.0, 1.0, 1.0)) 7 List(0, 27, List(0, 1, 2, 5, 10, 11, 12, 15, 17, 22, 24), List(1.0, 1.0, 8.0, 1.0, 1.0, 29.0, 64.0, 93.46056782334385, 1.0, 1.0, 1.0)) 9 List(0, 27, List(0, 1, 2, 5, 10, 11, 12, 15, 17, 22, 24), List(2.0, 1.0, 9.0, 1.0, 1.0, 71.0, 67.0, 93.46056782334385, 1.0, 1.0, 1.0)) 39 List(0, 27, List(1, 2, 5, 10, 11, 12, 14, 15, 17, 22, 24), List(1.0, 10.0, 1.0, 1.0, 46.0, 86.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 List(0, 27, List(0, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 11.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 39.0, 41.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 12.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 21.0, 62.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 13.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 42.0, 40.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 14.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 40.0, 78.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 5, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 15.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 38.0, 61.0, 93.46056782334385, 1.0, 1.0, 1.0)) 12 List(0, 27, List(2, 6, 8, 9, 10, 11, 12, 15, 17, 23, 24), List(5.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 27.0, 43.0, 93.46056782334385, 1.0, 1.0, 1.0)) 19 List(0, 27, List(0, 2, 4, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 18.0, 1.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 73.0, 33.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 19.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 16.0, 52.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 1.0, 20.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 81.0, 46.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 List(0, 27, List(0, 1, 2, 6, 8, 9, 10, 11, 12, 15, 17, 23, 24), List(1.0, 1.0, 1.0, 1.0, 2.0, 0.5195839405059814, 0.8544194102287292, 48.0, 32.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 1, 2, 5, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(4.0, 1.0, 22.0, 1.0, 2.0, 0.5195839405059814, 0.8544194102287292, 24.0, 89.0, 93.46056782334385, 1.0, 1.0, 1.0)) 8 List(0, 27, List(0, 1, 2, 6, 8, 9, 10, 11, 12, 15, 17, 23, 24), List(5.0, 1.0, 2.0, 1.0, 2.0, 0.5195839405059814, 0.8544194102287292, 51.0, 32.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 1.0, 23.0, 1.0, 1.0, 2.0, 0.5195839405059814, 0.8544194102287292, 13.0, 81.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 2, 4, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 24.0, 1.0, 1.0, 1.0, 2.0, 0.51958

In [8]:
test_df=spark.read.parquet('/FileStore/my-stuff/df_test_final.parquet')
display(test_df)

created_utc domain num_comments score subreddit idx index is_crosspostable_encoded domaintfidf timestamp total_subreddit_posts subreddit_hotness subreddit_author_count binned_score author_cakeday_encoded author_flair_text_color_encoded brand_safe_encoded no_follow_enc over_18_enc subreddit_rev create_hour DOW DOW_value created_hour_sin created_hour_cos length_title titlewordCount url_length has_exclamation_mark has_question_mark average_da resultIndex lastIndex protocolIndex result1Index subreddit_rev_Index DOW_Index whitelist_statusIndex subreddit_typeIndex result_ohe DOW_ohe subreddit_type_ohe total_author_score_ntile_ohe whitelist_status_ohe subreddit_rev_ohe avg_author_score_ntile_ohe result1_ohe last_ohe protocol_ohe 1143988850 australia-hotel.blogspot.com 0 0 reddit.com 462 463 0 List(0, 262144, List(19859, 70954, 175575), List(6.07073772800249, 7.492123408933651, 2.208919680195662)) 2006-04-02T14:40:50.000+0000 9945 317 2079 1 0 0 1 1 0 reddit.com 14 Sun 1 -0.63108796 -0.7757113 16 2 29 0 0 93.46056782334385 2.0 0.0 0.0 0.0 0.0 6.0 0.0 0.0 List(0, 3, List(2), List(1.0)) List(0, 6, List(), List()) List(0, 2, List(0), List(1.0)) List(0, 10, List(), List()) List(0, 2, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 10, List(), List()) List(0, 3, List(0), List(1.0)) List(0, 27, List(0), List(1.0)) List(0, 6, List(0), List(1.0)) 1143991658 mobileherald.com 0 2 reddit.com 470 471 1 List(0, 262144, List(100580), List(8.051739196869073)) 2006-04-02T15:27:38.000+0000 9945 323 2079 1 0 0 1 1 0 reddit.com 15 Sun 1 -0.8169699 -0.5766803 44 8 32 0 0 93.46056782334385 1.0 0.0 0.0 0.0 0.0 6.0 0.0 0.0 List(0, 3, List(1), List(1.0)) List(0, 6, List(), List()) List(0, 2, List(0), List(1.0)) List(0, 10, List(7), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 10, List(7), List(1.0)) List(0, 3, List(0), List(1.0)) List(0, 27, List(0), List(1.0)) List(0, 6, List(0), List(1.0)) 1144000558 letsbesensible.blogspot.com 0 0 reddit.com 495 496 1 List(0, 262144, List(124556, 175575), List(8.744886377429019, 2.208919680195662)) 2006-04-02T17:55:58.000+0000 9945 342 2079 1 0 1 1 1 0 reddit.com 17 Sun 1 -0.99766874 -0.068242416 27 4 68 0 0 93.46056782334385 1.0 0.0 0.0 0.0 0.0 6.0 0.0 0.0 List(0, 3, List(1), List(1.0)) List(0, 6, List(), List()) List(0, 2, List(0), List(1.0)) List(0, 10, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 10, List(2), List(1.0)) List(0, 3, List(0), List(1.0)) List(0, 27, List(0), List(1.0)) List(0, 6, List(0), List(1.0)) 1144121883 videosift.com 0 0 reddit.com 1087 1088 0 List(0, 262144, List(127425), List(5.972297655189237)) 2006-04-04T03:38:03.000+0000 9945 774 2079 1 0 0 1 1 0 reddit.com 3 Tue 3 0.730836 0.6825532 35 5 34 1 0 93.46056782334385 1.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 List(0, 3, List(1), List(1.0)) List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(6), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 10, List(7), List(1.0)) List(0, 3, List(0), List(1.0)) List(0, 27, List(0), List(1.0)) List(0, 6, List(0), List(1.0)) 1144156492 uncommonbusiness.blogspot.com 1 0 reddit.com 1237 1238 1 List(0, 262144, List(169754, 175575, 232421), List(6.219157733120763, 2.208919680195662, 6.179937019967482)) 2006-04-04T13:14:52.000+0000 9945 888 2079 1 0 0 1 1 0 reddit.com 13 Tue 3 -0.39840108 -0.9172113 43 5 80 0 0 93.46056782334385 2.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 List(0, 3, List(2), List(1.0)) List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(8), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 14, List(0), List(1.0)) List(0, 10, List(8), List(1.0)) List(0, 3, List(0), List(1.0)) List(0, 27, List(0), List(1.0)) List(0, 6, List(0), List(1.0)) 1144173130 emailbattles.com 0 4 reddit.com 1341 1342 1 List(0, 262144, List(241376), List(6.604820213932748)) 2006-04-04T17:52:10.000+0000 9945 979 2079 1 0 0 1 0 0 reddit.com 17 Tue 3 -0.99766874 -0.068242416 55 

In [9]:
#Drop Redundant features
test_df=test_df.drop('created_utc','domain','subreddit','idx','index','timestamp','subreddit_rev','DOW','DOW_value','whitelist_statusIndex','whitelist_status_ohe','binned_score','DOW_Index','resultIndex','lastIndex','protocolIndex','result1Index','subreddit_rev_Index','subreddit_typeIndex','domaintfidf','total_author_score_ntile_ohe','subreddit_author_count','total_subreddit_posts','titlewordCount','avg_author_score_ntile_ohe','result_ohe','subreddit_rev_ohe','last_ohe','protocol_ohe','created_hour')
display(test_df)

num_comments score is_crosspostable_encoded subreddit_hotness author_cakeday_encoded author_flair_text_color_encoded brand_safe_encoded no_follow_enc over_18_enc create_hour created_hour_sin created_hour_cos length_title url_length has_exclamation_mark has_question_mark average_da DOW_ohe subreddit_type_ohe result1_ohe 0 0 0 317 0 0 1 1 0 14 -0.63108796 -0.7757113 16 29 0 0 93.46056782334385 List(0, 6, List(), List()) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 2 1 323 0 0 1 1 0 15 -0.8169699 -0.5766803 44 32 0 0 93.46056782334385 List(0, 6, List(), List()) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 342 0 1 1 1 0 17 -0.99766874 -0.068242416 27 68 0 0 93.46056782334385 List(0, 6, List(), List()) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 0 774 0 0 1 1 0 3 0.730836 0.6825532 35 34 1 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 0 1 888 0 0 1 1 0 13 -0.39840108 -0.9172113 43 80 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 4 1 979 0 0 1 0 0 17 -0.99766874 -0.068242416 55 60 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(1), List(1.0)) 1 0 1 70 0 0 1 1 0 5 0.9790841 0.20345601 13 21 0 0 93.46056782334385 List(0, 6, List(0), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 1218 0 0 1 1 0 8 0.8169699 -0.5766803 43 60 0 0 93.46056782334385 List(0, 6, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 0 1 1473 0 0 1 1 0 20 -0.730836 0.6825532 62 75 0 0 93.46056782334385 List(0, 6, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 97 0 0 1 1 0 5 0.9790841 0.20345601 27 27 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 7 46 1 1793 0 0 1 0 0 16 -0.9422609 -0.3348796 54 47 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 1 2049 0 0 1 1 0 13 -0.39840108 -0.9172113 74 97 0 0 93.46056782334385 List(0, 6, List(4), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 1 2284 0 0 1 1 0 22 -0.26979676 0.96291727 35 60 0 0 93.46056782334385 List(0, 6, List(5), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 0 2410 0 0 1 1 0 19 -0.8878852 0.46006504 12 46 0 0 93.46056782334385 List(0, 6, List(3), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 2449 0 1 1 1 0 1 0.26979676 0.96291727 33 51 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 2 0 1 2432 0 0 1 1 0 6 0.99766874 -0.068242416 44 76 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 2426 0 0 1 1 0 13 -0.39840108 -0.9172113 86 161 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 0 2422 0 0 1 1 0 12 -0.13616665 -0.99068594 30 69 0 0 93.46056782334385 List(0, 6, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 3 0 1 9 0 0 0 1 0 0 0.0 1.0 67 73 0 1 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 0 2384 0 0 1 1 0 5 0.9790841 0.20345601 10 53 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 3 0 113 0 1 1 1 0 9 0.63108796 -0.7757113 31 61 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 85 0 0 0 1 1 19 -0.8878852 0.46006504 45 46 1 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 0 9 1 2371 0 0 1 0 0 2 0.51958394 0.8544194 45 3

In [10]:
display(test_df.describe())

summary num_comments score is_crosspostable_encoded subreddit_hotness author_cakeday_encoded author_flair_text_color_encoded brand_safe_encoded no_follow_enc over_18_enc create_hour created_hour_sin created_hour_cos length_title url_length has_exclamation_mark has_question_mark average_da count 12302 12302 12302 12302 12302 12302 12302 12302 12302 12302 12302 12302 12302 12302 12302 12302 12302 mean 1.4669972362217525 7.9349699235896605 0.7454885384490326 1685.5210534872379 0.016257519102584946 0.07055763290521866 0.8489676475369858 0.7778410014631767 0.04926028288083238 12.816615184522842 -0.17729896798892208 0.013250692966623512 44.800520240611284 53.99382214274102 0.03893675825069094 0.05958380751097383 93.44348484345555 stddev 6.660560645667689 29.477351181187235 0.4356039507127872 982.2082579734872 0.1264694126287568 0.2560948741330291 0.3580949659571148 0.41571435613921354 0.21641976508693506 6.613711690965638 0.6932162929276409 0.6985122605404028 23.71678077487728 24.1098877327853 0.19345213669685685 0.23672374743258245 0.18058192574268525 min 0 0 0 1 0 0 0 0 0 0 -0.99766874 -0.99068594 0 8 0 0 92.0 max 317 437 1 2531 1 1 1 1 1 23 0.99766874 1.0 576 288 1 1 97.0

In [11]:
X_test=test_df.drop('score')
display(X_test)

num_comments is_crosspostable_encoded subreddit_hotness author_cakeday_encoded author_flair_text_color_encoded brand_safe_encoded no_follow_enc over_18_enc create_hour created_hour_sin created_hour_cos length_title url_length has_exclamation_mark has_question_mark average_da DOW_ohe subreddit_type_ohe result1_ohe 0 0 317 0 0 1 1 0 14 -0.63108796 -0.7757113 16 29 0 0 93.46056782334385 List(0, 6, List(), List()) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 323 0 0 1 1 0 15 -0.8169699 -0.5766803 44 32 0 0 93.46056782334385 List(0, 6, List(), List()) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 342 0 1 1 1 0 17 -0.99766874 -0.068242416 27 68 0 0 93.46056782334385 List(0, 6, List(), List()) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 774 0 0 1 1 0 3 0.730836 0.6825532 35 34 1 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 1 888 0 0 1 1 0 13 -0.39840108 -0.9172113 43 80 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 979 0 0 1 0 0 17 -0.99766874 -0.068242416 55 60 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(1), List(1.0)) 1 1 70 0 0 1 1 0 5 0.9790841 0.20345601 13 21 0 0 93.46056782334385 List(0, 6, List(0), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 1218 0 0 1 1 0 8 0.8169699 -0.5766803 43 60 0 0 93.46056782334385 List(0, 6, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 1 1473 0 0 1 1 0 20 -0.730836 0.6825532 62 75 0 0 93.46056782334385 List(0, 6, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 97 0 0 1 1 0 5 0.9790841 0.20345601 27 27 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 7 1 1793 0 0 1 0 0 16 -0.9422609 -0.3348796 54 47 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 2049 0 0 1 1 0 13 -0.39840108 -0.9172113 74 97 0 0 93.46056782334385 List(0, 6, List(4), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 2284 0 0 1 1 0 22 -0.26979676 0.96291727 35 60 0 0 93.46056782334385 List(0, 6, List(5), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 2410 0 0 1 1 0 19 -0.8878852 0.46006504 12 46 0 0 93.46056782334385 List(0, 6, List(3), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 2449 0 1 1 1 0 1 0.26979676 0.96291727 33 51 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 2 1 2432 0 0 1 1 0 6 0.99766874 -0.068242416 44 76 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 2426 0 0 1 1 0 13 -0.39840108 -0.9172113 86 161 0 0 93.46056782334385 List(0, 6, List(1), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 2422 0 0 1 1 0 12 -0.13616665 -0.99068594 30 69 0 0 93.46056782334385 List(0, 6, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 3 1 9 0 0 0 1 0 0 0.0 1.0 67 73 0 1 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 2384 0 0 1 1 0 5 0.9790841 0.20345601 10 53 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 113 0 1 1 1 0 9 0.63108796 -0.7757113 31 61 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 85 0 0 0 1 1 19 -0.8878852 0.46006504 45 46 1 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 2371 0 0 1 0 0 2 0.51958394 0.8544194 45 30 0 0 93.46056782334385 List(0, 6, List(4), List(1.0)

In [12]:
print(X_test.columns)

['num_comments', 'is_crosspostable_encoded', 'subreddit_hotness', 'author_cakeday_encoded', 'author_flair_text_color_encoded', 'brand_safe_encoded', 'no_follow_enc', 'over_18_enc', 'create_hour', 'created_hour_sin', 'created_hour_cos', 'length_title', 'url_length', 'has_exclamation_mark', 'has_question_mark', 'average_da', 'DOW_ohe', 'subreddit_type_ohe', 'result1_ohe']

In [13]:
print(X_train.columns)

['num_comments', 'is_crosspostable_encoded', 'subreddit_hotness', 'author_cakeday_encoded', 'author_flair_text_color_encoded', 'brand_safe_encoded', 'no_follow_enc', 'over_18_enc', 'create_hour', 'created_hour_sin', 'created_hour_cos', 'length_title', 'url_length', 'has_exclamation_mark', 'has_question_mark', 'average_da', 'DOW_ohe', 'subreddit_type_ohe', 'result1_ohe']

In [14]:
vect_asmb_2=VectorAssembler(inputCols=X_test.columns,outputCol='features')
testing_df=vect_asmb_2.transform(test_df).select('features','score')
display(testing_df)

features score List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 22, 24), List(317.0, 1.0, 1.0, 14.0, -0.6310879588127136, -0.7757112979888916, 16.0, 29.0, 93.46056782334385, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 22, 24), List(1.0, 323.0, 1.0, 1.0, 15.0, -0.8169698715209961, -0.5766803026199341, 44.0, 32.0, 93.46056782334385, 1.0, 1.0)) 2 List(0, 27, List(1, 2, 4, 5, 6, 8, 9, 10, 11, 12, 15, 22, 24), List(1.0, 342.0, 1.0, 1.0, 1.0, 17.0, -0.9976687431335449, -0.06824241578578949, 27.0, 68.0, 93.46056782334385, 1.0, 1.0)) 0 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 13, 15, 17, 22, 24), List(774.0, 1.0, 1.0, 3.0, 0.7308359742164612, 0.6825531721115112, 35.0, 34.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 1.0, 888.0, 1.0, 1.0, 13.0, -0.39840108156204224, -0.9172112941741943, 43.0, 80.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 5, 8, 9, 10, 11, 12, 15, 17, 22, 25), List(1.0, 979.0, 1.0, 17.0, -0.9976687431335449, -0.06824241578578949, 55.0, 60.0, 93.46056782334385, 1.0, 1.0, 1.0)) 4 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 16, 23, 24), List(1.0, 1.0, 70.0, 1.0, 1.0, 5.0, 0.9790840744972229, 0.20345601439476013, 13.0, 21.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 16, 22, 24), List(1.0, 1218.0, 1.0, 1.0, 8.0, 0.8169698715209961, -0.5766803026199341, 43.0, 60.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 16, 22, 24), List(1.0, 1.0, 1473.0, 1.0, 1.0, 20.0, -0.7308359742164612, 0.6825531721115112, 62.0, 75.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 23, 24), List(1.0, 97.0, 1.0, 1.0, 5.0, 0.9790840744972229, 0.20345601439476013, 27.0, 27.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 1, 2, 5, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(7.0, 1.0, 1793.0, 1.0, 16.0, -0.9422609210014343, -0.334879606962204, 54.0, 47.0, 93.46056782334385, 1.0, 1.0, 1.0)) 46 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 20, 22, 24), List(1.0, 2049.0, 1.0, 1.0, 13.0, -0.39840108156204224, -0.9172112941741943, 74.0, 97.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 21, 22, 24), List(1.0, 2284.0, 1.0, 1.0, 22.0, -0.269796758890152, 0.9629172682762146, 35.0, 60.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 19, 22, 24), List(2410.0, 1.0, 1.0, 19.0, -0.8878852128982544, 0.4600650370121002, 12.0, 46.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 4, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 2449.0, 1.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 33.0, 51.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(2.0, 1.0, 2432.0, 1.0, 1.0, 6.0, 0.9976687431335449, -0.06824241578578949, 44.0, 76.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 2426.0, 1.0, 1.0, 13.0, -0.39840108156204224, -0.9172112941741943, 86.0, 161.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 16, 22, 24), List(2422.0, 1.0, 1.0, 12.0, -0.13616664707660675, -0.9906859397888184, 30.0, 69.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 1, 2, 6, 10, 11, 12, 14, 15, 18, 23, 24), List(3.0, 1.0, 9.0, 1.0, 1.0, 67.0, 73.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(2384.0, 1.0, 1.0, 5.0, 0.9790840744972229, 0.20345601439476013, 10.0, 53.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(2, 4, 5, 6, 8, 9, 10, 11, 12, 15, 18, 23, 24), List(113.0, 1.0, 1.0, 1.0, 9.0, 0.6310879588127136, -0.7757112979888916, 31.0, 61.0, 93.46056782334385, 1.0, 1.0, 1.0)) 3 List(0, 27, List(1, 2, 6, 7, 8, 9, 10, 11, 12, 13, 15, 18, 23, 24), List(1.0, 85.0, 1.0, 1.0, 19.0, -0.

Random forest Regressor , Model Selection and Model Verification done by Abhishek

In [16]:
#Creation and fitting of base model
rf=RandomForestRegressor(numTrees=150,maxDepth=6,featuresCol='features',labelCol='score')
model=rf.fit(training_df)
train_pred_df_rf=model.transform(training_df)
display(train_pred_df_rf)

features score prediction List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 17, 22, 24), List(1.0, 1.0, 1.0, 1.0, 1.0, 20.0, 47.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.2490540287798177 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 17, 22, 24), List(1.0, 2.0, 1.0, 1.0, 1.0, 94.0, 44.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.5298075560360171 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 17, 22, 24), List(1.0, 3.0, 1.0, 1.0, 1.0, 61.0, 51.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.00542596129435 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 17, 22, 24), List(1.0, 5.0, 1.0, 1.0, 1.0, 31.0, 55.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.9365685747231642 List(0, 27, List(0, 1, 2, 5, 6, 10, 11, 12, 15, 17, 22, 24), List(1.0, 1.0, 6.0, 1.0, 1.0, 1.0, 17.0, 31.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.3469932856911377 List(0, 27, List(2, 6, 10, 11, 12, 15, 17, 24), List(1.0, 1.0, 1.0, 61.0, 12.0, 93.46056782334385, 1.0, 1.0)) 4 1.8431345080937966 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 17, 22, 24), List(1.0, 7.0, 1.0, 1.0, 1.0, 34.0, 58.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.9095901613112185 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 17, 23, 24), List(1.0, 1.0, 1.0, 1.0, 1.0, 32.0, 69.0, 93.46056782334385, 1.0, 1.0, 1.0)) 7 3.915767642345234 List(0, 27, List(0, 1, 2, 5, 10, 11, 12, 15, 17, 22, 24), List(1.0, 1.0, 8.0, 1.0, 1.0, 29.0, 64.0, 93.46056782334385, 1.0, 1.0, 1.0)) 9 15.300686977503123 List(0, 27, List(0, 1, 2, 5, 10, 11, 12, 15, 17, 22, 24), List(2.0, 1.0, 9.0, 1.0, 1.0, 71.0, 67.0, 93.46056782334385, 1.0, 1.0, 1.0)) 39 21.68732733736005 List(0, 27, List(1, 2, 5, 10, 11, 12, 14, 15, 17, 22, 24), List(1.0, 10.0, 1.0, 1.0, 46.0, 86.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 12.908409741228098 List(0, 27, List(0, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 11.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 39.0, 41.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.7802319799835754 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 12.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 21.0, 62.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.939361741534137 List(0, 27, List(0, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 13.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 42.0, 40.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.7231710376757389 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 14.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 40.0, 78.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.0228515563813882 List(0, 27, List(1, 2, 5, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 15.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 38.0, 61.0, 93.46056782334385, 1.0, 1.0, 1.0)) 12 12.988645265861315 List(0, 27, List(2, 6, 8, 9, 10, 11, 12, 15, 17, 23, 24), List(5.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 27.0, 43.0, 93.46056782334385, 1.0, 1.0, 1.0)) 19 2.0623536577105357 List(0, 27, List(0, 2, 4, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 18.0, 1.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 73.0, 33.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.7842871603288399 List(0, 27, List(0, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 19.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 16.0, 52.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.6533587181642729 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 1.0, 20.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 81.0, 46.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 1.2114084787434547 List(0, 27, List(0, 1, 2, 6, 8, 9, 10, 11, 12, 15, 17, 23, 24), List(1.0, 1.0, 1.0, 1.0, 2.0, 0.5195839405059814, 0.8544194102287292, 48.0, 32.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 2.2129879756536766 List(0, 27, List(0, 1, 2, 5, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(4.0, 1.0, 22.0, 1.0, 2.0, 0.5195839405059814, 0.8544194102287292, 24.0, 89.0, 93.46056782334385, 1.0, 1.0, 1.0)) 8 38.30625112202801 List(0, 27, List(0, 1, 2, 6, 8, 9, 10, 11, 12, 15, 17, 23, 24)

In [17]:
prediction_df=model.transform(testing_df)
display(prediction_df)

features score prediction List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 22, 24), List(317.0, 1.0, 1.0, 14.0, -0.6310879588127136, -0.7757112979888916, 16.0, 29.0, 93.46056782334385, 1.0, 1.0)) 0 0.5562754861106067 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 22, 24), List(1.0, 323.0, 1.0, 1.0, 15.0, -0.8169698715209961, -0.5766803026199341, 44.0, 32.0, 93.46056782334385, 1.0, 1.0)) 2 0.702891485024798 List(0, 27, List(1, 2, 4, 5, 6, 8, 9, 10, 11, 12, 15, 22, 24), List(1.0, 342.0, 1.0, 1.0, 1.0, 17.0, -0.9976687431335449, -0.06824241578578949, 27.0, 68.0, 93.46056782334385, 1.0, 1.0)) 0 0.7440968995525238 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 13, 15, 17, 22, 24), List(774.0, 1.0, 1.0, 3.0, 0.7308359742164612, 0.6825531721115112, 35.0, 34.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.39038368217901576 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 1.0, 888.0, 1.0, 1.0, 13.0, -0.39840108156204224, -0.9172112941741943, 43.0, 80.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.5857239717639412 List(0, 27, List(1, 2, 5, 8, 9, 10, 11, 12, 15, 17, 22, 25), List(1.0, 979.0, 1.0, 17.0, -0.9976687431335449, -0.06824241578578949, 55.0, 60.0, 93.46056782334385, 1.0, 1.0, 1.0)) 4 13.678802897924582 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 16, 23, 24), List(1.0, 1.0, 70.0, 1.0, 1.0, 5.0, 0.9790840744972229, 0.20345601439476013, 13.0, 21.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 2.977963107604011 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 16, 22, 24), List(1.0, 1218.0, 1.0, 1.0, 8.0, 0.8169698715209961, -0.5766803026199341, 43.0, 60.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.582114845257254 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 16, 22, 24), List(1.0, 1.0, 1473.0, 1.0, 1.0, 20.0, -0.7308359742164612, 0.6825531721115112, 62.0, 75.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.7004146352754176 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 23, 24), List(1.0, 97.0, 1.0, 1.0, 5.0, 0.9790840744972229, 0.20345601439476013, 27.0, 27.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 2.8383580565110305 List(0, 27, List(0, 1, 2, 5, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(7.0, 1.0, 1793.0, 1.0, 16.0, -0.9422609210014343, -0.334879606962204, 54.0, 47.0, 93.46056782334385, 1.0, 1.0, 1.0)) 46 84.72306932807386 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 20, 22, 24), List(1.0, 2049.0, 1.0, 1.0, 13.0, -0.39840108156204224, -0.9172112941741943, 74.0, 97.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 0.6712001423484997 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 21, 22, 24), List(1.0, 2284.0, 1.0, 1.0, 22.0, -0.269796758890152, 0.9629172682762146, 35.0, 60.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 0.5735591124664282 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 19, 22, 24), List(2410.0, 1.0, 1.0, 19.0, -0.8878852128982544, 0.4600650370121002, 12.0, 46.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.35946496552611057 List(0, 27, List(1, 2, 4, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 2449.0, 1.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 33.0, 51.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.9250610775690495 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(2.0, 1.0, 2432.0, 1.0, 1.0, 6.0, 0.9976687431335449, -0.06824241578578949, 44.0, 76.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.7640601252963555 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 2426.0, 1.0, 1.0, 13.0, -0.39840108156204224, -0.9172112941741943, 86.0, 161.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.6957303464118343 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 16, 22, 24), List(2422.0, 1.0, 1.0, 12.0, -0.13616664707660675, -0.9906859397888184, 30.0, 69.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.39112875670111547 List(0, 27, List(0, 1, 2, 6, 10, 11, 12, 14, 15, 18, 23, 24), List(3.0, 1.0, 9.0, 1.0, 1.0, 67.0, 73.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 7.066754867758712 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(2384.0, 1.0, 1.0, 5.0, 0.9790840

In [18]:
#Evalution of the model 
eval_1 = RegressionEvaluator(labelCol="score", predictionCol="prediction", metricName="rmse")
train_rmse_rf=eval_1.evaluate(train_pred_df_rf)
rmse=eval_1.evaluate(prediction_df)
print('RMSE value of random forest regression model for train:',train_rmse_rf)
print('RMSE value of random forest regression model for test:',rmse)

RMSE value of random forest regression model for train: 17.725873413697062
RMSE value of random forest regression model for test: 18.8537125004005

In [19]:
eval_2 = RegressionEvaluator(labelCol="score", predictionCol="prediction", metricName="r2")
train_r2_rf=eval_2.evaluate(train_pred_df_rf)
r2=eval_2.evaluate(prediction_df)
print('R-square value of random forest regression model for train:', train_r2_rf)
print('R-square value of random forest regression model for test:', r2)

R-square value of random forest regression model for train: 0.6363330835601892
R-square value of random forest regression model for test: 0.5908786405779651

In [20]:
paramGrid = ParamGridBuilder().addGrid(rf.numTrees,[90,95,100]).addGrid(rf.maxDepth,[5,6,7]).build()
ev=RegressionEvaluator(labelCol="score", predictionCol="prediction")
crossval = CrossValidator(estimator=rf, estimatorParamMaps=paramGrid, evaluator=ev, numFolds=5, parallelism=10)

In [21]:
cv=crossval.fit(training_df)
train_pred_rf_cv=cv.transform(training_df)
prediction_cv=cv.transform(testing_df)
display(prediction_cv)

features score prediction List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 22, 24), List(317.0, 1.0, 1.0, 14.0, -0.6310879588127136, -0.7757112979888916, 16.0, 29.0, 93.46056782334385, 1.0, 1.0)) 0 0.3177230066001132 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 22, 24), List(1.0, 323.0, 1.0, 1.0, 15.0, -0.8169698715209961, -0.5766803026199341, 44.0, 32.0, 93.46056782334385, 1.0, 1.0)) 2 0.6362672169787429 List(0, 27, List(1, 2, 4, 5, 6, 8, 9, 10, 11, 12, 15, 22, 24), List(1.0, 342.0, 1.0, 1.0, 1.0, 17.0, -0.9976687431335449, -0.06824241578578949, 27.0, 68.0, 93.46056782334385, 1.0, 1.0)) 0 0.7004935778193848 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 13, 15, 17, 22, 24), List(774.0, 1.0, 1.0, 3.0, 0.7308359742164612, 0.6825531721115112, 35.0, 34.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.28128339884483083 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 1.0, 888.0, 1.0, 1.0, 13.0, -0.39840108156204224, -0.9172112941741943, 43.0, 80.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.643644885697688 List(0, 27, List(1, 2, 5, 8, 9, 10, 11, 12, 15, 17, 22, 25), List(1.0, 979.0, 1.0, 17.0, -0.9976687431335449, -0.06824241578578949, 55.0, 60.0, 93.46056782334385, 1.0, 1.0, 1.0)) 4 11.819035564536275 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 16, 23, 24), List(1.0, 1.0, 70.0, 1.0, 1.0, 5.0, 0.9790840744972229, 0.20345601439476013, 13.0, 21.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 2.8080812824615973 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 16, 22, 24), List(1.0, 1218.0, 1.0, 1.0, 8.0, 0.8169698715209961, -0.5766803026199341, 43.0, 60.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.45914862586035665 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 16, 22, 24), List(1.0, 1.0, 1473.0, 1.0, 1.0, 20.0, -0.7308359742164612, 0.6825531721115112, 62.0, 75.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.5863947132999507 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 23, 24), List(1.0, 97.0, 1.0, 1.0, 5.0, 0.9790840744972229, 0.20345601439476013, 27.0, 27.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 2.9351937822313348 List(0, 27, List(0, 1, 2, 5, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(7.0, 1.0, 1793.0, 1.0, 16.0, -0.9422609210014343, -0.334879606962204, 54.0, 47.0, 93.46056782334385, 1.0, 1.0, 1.0)) 46 81.28002245870006 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 20, 22, 24), List(1.0, 2049.0, 1.0, 1.0, 13.0, -0.39840108156204224, -0.9172112941741943, 74.0, 97.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 0.4634083683590996 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 21, 22, 24), List(1.0, 2284.0, 1.0, 1.0, 22.0, -0.269796758890152, 0.9629172682762146, 35.0, 60.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 0.44719518683440396 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 19, 22, 24), List(2410.0, 1.0, 1.0, 19.0, -0.8878852128982544, 0.4600650370121002, 12.0, 46.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.2646713664745906 List(0, 27, List(1, 2, 4, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 2449.0, 1.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 33.0, 51.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.955787886012502 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(2.0, 1.0, 2432.0, 1.0, 1.0, 6.0, 0.9976687431335449, -0.06824241578578949, 44.0, 76.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 2.2326718394479745 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 17, 22, 24), List(1.0, 2426.0, 1.0, 1.0, 13.0, -0.39840108156204224, -0.9172112941741943, 86.0, 161.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.46546784918909795 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 16, 22, 24), List(2422.0, 1.0, 1.0, 12.0, -0.13616664707660675, -0.9906859397888184, 30.0, 69.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.35731916605427455 List(0, 27, List(0, 1, 2, 6, 10, 11, 12, 14, 15, 18, 23, 24), List(3.0, 1.0, 9.0, 1.0, 1.0, 67.0, 73.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 4.076161175632243 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(2384.0, 1.0, 1.0, 5.0, 0.9790

In [22]:
rmse2=eval_1.evaluate(train_pred_df_rf)
r2_cv_train=eval_2.evaluate(train_pred_df_rf)
print('RMSE value of cv random forest regression model for train:',rmse2)
print('R-square value of cv random forest regression model for train:', r2_cv_train)

RMSE value of cv random forest regression model for train: 17.725873413697062
R-square value of cv random forest regression model for train: 0.6363330835601892

In [23]:
rmse2_test=eval_1.evaluate(prediction_cv)
r2_cv_test=eval_2.evaluate(prediction_cv)
print('RMSE value of cv random forest regression model for test:',rmse2_test)
print('R-square value of cv random forest regression model for test:', r2_cv_test)

RMSE value of cv random forest regression model for test: 19.090542798617573
R-square value of cv random forest regression model for test: 0.580535755747204

In [24]:
best_model = cv.bestModel
Param_list = best_model.extractParamMap()
Param_list

Out[23]: {Param(parent='RandomForestRegressor_fd7d3a9fb7be', name='cacheNodeIds', doc='If false, the algorithm will pass trees to executors to match instances with nodes. If true, the algorithm will cache node IDs for each instance. Caching can speed up training of deeper trees.'): False,
 Param(parent='RandomForestRegressor_fd7d3a9fb7be', name='checkpointInterval', doc='set checkpoint interval (>= 1) or disable checkpoint (-1). E.g. 10 means that the cache will get checkpointed every 10 iterations. Note: this setting will be ignored if the checkpoint directory is not set in the SparkContext'): 10,
 Param(parent='RandomForestRegressor_fd7d3a9fb7be', name='featureSubsetStrategy', doc='The number of features to consider for splits at each tree node. Supported options: auto, all, onethird, sqrt, log2, (0.0-1.0], [1-n].'): 'auto',
 Param(parent='RandomForestRegressor_fd7d3a9fb7be', name='featuresCol', doc='features column name'): 'features',
 Param(parent='RandomForestRegressor_fd7d3a9fb7be', name='impurity', doc='Criterion used for information gain calculation (case-insensitive). Supported options: variance'): 'variance',
 Param(parent='RandomForestRegressor_fd7d3a9fb7be', name='labelCol', doc='label column name'): 'score',
 Param(parent='RandomForestRegressor_fd7d3a9fb7be', name='maxBins', doc='Max number of bins for discretizing continuous features. Must be at least 2 and at least number of categories for any categorical feature.'): 32,
 Param(parent='RandomForestRegressor_fd7d3a9fb7be', name='maxDepth', doc='Maximum depth of the tree. (Nonnegative) E.g., depth 0 means 1 leaf node; depth 1 means 1 internal node + 2 leaf nodes.'): 7,
 Param(parent='RandomForestRegressor_fd7d3a9fb7be', name='maxMemoryInMB', doc='Maximum memory in MB allocated to histogram aggregation.'): 256,
 Param(parent='RandomForestRegressor_fd7d3a9fb7be', name='minInfoGain', doc='Minimum information gain for a split to be considered at a tree node.'): 0.0,
 Param(parent='RandomForestRegressor_fd7d3a9fb7be', name='minInstancesPerNode', doc='Minimum number of instances each child must have after split. If a split causes the left or right child to have fewer than minInstancesPerNode, the split will be discarded as invalid. Must be at least 1.'): 1,
 Param(parent='RandomForestRegressor_fd7d3a9fb7be', name='numTrees', doc='Number of trees to train (at least 1)'): 95,
 Param(parent='RandomForestRegressor_fd7d3a9fb7be', name='predictionCol', doc='prediction column name'): 'prediction',
 Param(parent='RandomForestRegressor_fd7d3a9fb7be', name='seed', doc='random seed'): 2502083311556356884,
 Param(parent='RandomForestRegressor_fd7d3a9fb7be', name='subsamplingRate', doc='Fraction of the training data used for learning each decision tree, in range (0, 1].'): 1.0}

In [25]:
#Load the OOT Dataset
oot_df=spark.read.parquet('/FileStore/my-stuff/df_oot_final.parquet')
display(oot_df)

num_comments score is_crosspostable_encoded total_subreddit_posts subreddit_hotness subreddit_author_count binned_score author_cakeday_encoded author_flair_text_color_encoded brand_safe_encoded no_follow_enc over_18_enc create_hour created_hour_sin created_hour_cos length_title titlewordCount url_length has_exclamation_mark has_question_mark average_da result1Index result_ohe DOW_ohe subreddit_type_ohe total_author_score_ntile_ohe subreddit_rev_ohe avg_author_score_ntile_ohe result1_ohe last_ohe protocol_ohe 1 0 0 11842 1 2458 1 0 0 1 1 0 0 0.0 1.0 69 14 50 0 1 93.46056782334385 2.0 List(0, 2, List(0), List(1.0)) List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(), List()) List(0, 11, List(0), List(1.0)) List(0, 10, List(), List()) List(0, 3, List(2), List(1.0)) List(0, 24, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) 2 0 1 11842 2 2458 1 0 0 1 1 0 0 0.0 1.0 30 6 73 0 1 93.46056782334385 0.0 List(0, 2, List(0), List(1.0)) List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(), List()) List(0, 11, List(0), List(1.0)) List(0, 10, List(), List()) List(0, 3, List(0), List(1.0)) List(0, 24, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) 0 0 1 11842 4 2458 1 0 0 1 1 0 0 0.0 1.0 38 5 62 0 1 93.46056782334385 0.0 List(0, 2, List(0), List(1.0)) List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(8), List(1.0)) List(0, 11, List(0), List(1.0)) List(0, 10, List(8), List(1.0)) List(0, 3, List(0), List(1.0)) List(0, 24, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) 0 1 1 11842 5 2458 1 0 0 1 0 0 0 0.0 1.0 75 11 63 0 0 93.46056782334385 0.0 List(0, 2, List(0), List(1.0)) List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(1), List(1.0)) List(0, 11, List(0), List(1.0)) List(0, 10, List(2), List(1.0)) List(0, 3, List(0), List(1.0)) List(0, 24, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) 3 11 1 359 1 47 1 0 0 0 1 0 0 0.0 1.0 24 2 26 0 0 93.46056782334385 1.0 List(0, 2, List(), List()) List(0, 6, List(2), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 10, List(4), List(1.0)) List(0, 11, List(4), List(1.0)) List(0, 10, List(4), List(1.0)) List(0, 3, List(1), List(1.0)) List(0, 24, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) 0 0 1 11842 6 2458 1 0 0 1 1 0 0 0.0 1.0 28 4 53 0 0 93.46056782334385 0.0 List(0, 2, List(0), List(1.0)) List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(), List()) List(0, 11, List(0), List(1.0)) List(0, 10, List(), List()) List(0, 3, List(0), List(1.0)) List(0, 24, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) 59 196 1 11842 7 2458 3 0 0 1 0 0 0 0.0 1.0 43 8 38 0 0 93.46056782334385 0.0 List(0, 2, List(1), List(1.0)) List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(3), List(1.0)) List(0, 11, List(0), List(1.0)) List(0, 10, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) List(0, 24, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) 0 1 1 11842 8 2458 1 0 0 1 1 0 0 0.0 1.0 31 5 34 0 0 93.46056782334385 0.0 List(0, 2, List(0), List(1.0)) List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(7), List(1.0)) List(0, 11, List(0), List(1.0)) List(0, 10, List(6), List(1.0)) List(0, 3, List(0), List(1.0)) List(0, 24, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) 0 0 0 11842 9 2458 1 0 1 1 1 0 0 0.0 1.0 46 7 42 0 0 93.46056782334385 0.0 List(0, 2, List(0), List(1.0)) List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(1), List(1.0)) List(0, 11, List(0), List(1.0)) List(0, 10, List(2), List(1.0)) List(0, 3, List(0), List(1.0)) List(0, 24, List(0), List(1.0)) List(0, 2, List(0), List(1.0)) 0 1 1 11842 10 2458 1 0 0 1 0 0 0 0.0 1.0 34 6 41 0 0 93.46056782334385 0.0 List(0, 2, List(), List()) List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 10, List(1), List(1.0)) List(0, 11, List(0), List(1.0)) List(0, 10, List(2), List(1.0)) List(0, 3, List(0), List(1.0)

In [26]:
#Model Selection and Verfication on OOT dataset

In [27]:
#Drop Redundant features
oot_df=oot_df.drop('created_utc','domain','subreddit','idx','index','timestamp','subreddit_rev','DOW','DOW_value','whitelist_statusIndex','whitelist_status_ohe','binned_score','DOW_Index','resultIndex','lastIndex','protocolIndex','result1Index','subreddit_rev_Index','subreddit_typeIndex','domaintfidf','total_author_score_ntile_ohe','subreddit_author_count','total_subreddit_posts','titlewordCount','avg_author_score_ntile_ohe','result_ohe','subreddit_rev_ohe','last_ohe','protocol_ohe','created_hour')
display(oot_df)

num_comments score is_crosspostable_encoded subreddit_hotness author_cakeday_encoded author_flair_text_color_encoded brand_safe_encoded no_follow_enc over_18_enc create_hour created_hour_sin created_hour_cos length_title url_length has_exclamation_mark has_question_mark average_da DOW_ohe subreddit_type_ohe result1_ohe 1 0 0 1 0 0 1 1 0 0 0.0 1.0 69 50 0 1 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(2), List(1.0)) 2 0 1 2 0 0 1 1 0 0 0.0 1.0 30 73 0 1 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 4 0 0 1 1 0 0 0.0 1.0 38 62 0 1 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 1 5 0 0 1 0 0 0 0.0 1.0 75 63 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 3 11 1 1 0 0 0 1 0 0 0.0 1.0 24 26 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(1), List(1.0)) 0 0 1 6 0 0 1 1 0 0 0.0 1.0 28 53 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 59 196 1 7 0 0 1 0 0 0 0.0 1.0 43 38 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 1 8 0 0 1 1 0 0 0.0 1.0 31 34 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 0 9 0 1 1 1 0 0 0.0 1.0 46 42 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 1 1 10 0 0 1 0 0 0 0.0 1.0 34 41 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 12 0 0 1 1 0 1 0.26979676 0.96291727 30 42 0 1 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 3 2 1 13 0 0 1 0 0 1 0.26979676 0.96291727 19 42 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 3 0 0 0 1 0 1 0.26979676 0.96291727 55 41 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(1), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 1 14 0 1 1 1 0 1 0.26979676 0.96291727 65 64 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 0 15 0 0 1 1 0 1 0.26979676 0.96291727 20 48 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 0 16 0 0 1 1 0 1 0.26979676 0.96291727 36 64 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 0 17 0 0 1 1 0 1 0.26979676 0.96291727 38 66 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 0 18 0 0 1 1 0 1 0.26979676 0.96291727 37 65 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 0 19 0 0 1 1 0 1 0.26979676 0.96291727 37 65 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 86 361 1 24 0 1 1 0 0 1 0.26979676 0.96291727 70 125 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 0 26 0 0 1 1 0 2 0.51958394 0.8544194 24 59 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 1 0 1 27 0 0 1 1 0 2 0.51958394 0.8544194 19 30 0 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 0 0 0 28 0 0 1 1 0 2 0.51958394 0.8544194 58 69 1 0 93.46056782334385 List(0, 6, List(2), List(1.0)) List(0, 2, List(0), List(1.0)) List(0, 3, List(0), List(1.0)) 7 83 1 29 0 0 1 0 0 2 0.51958394 0.8544194 80 77 0 0

In [28]:
X_oot=oot_df.drop('score')
print(X_oot.columns)

['num_comments', 'is_crosspostable_encoded', 'subreddit_hotness', 'author_cakeday_encoded', 'author_flair_text_color_encoded', 'brand_safe_encoded', 'no_follow_enc', 'over_18_enc', 'create_hour', 'created_hour_sin', 'created_hour_cos', 'length_title', 'url_length', 'has_exclamation_mark', 'has_question_mark', 'average_da', 'DOW_ohe', 'subreddit_type_ohe', 'result1_ohe']

In [29]:
print(X_train.columns)

['num_comments', 'is_crosspostable_encoded', 'subreddit_hotness', 'author_cakeday_encoded', 'author_flair_text_color_encoded', 'brand_safe_encoded', 'no_follow_enc', 'over_18_enc', 'create_hour', 'created_hour_sin', 'created_hour_cos', 'length_title', 'url_length', 'has_exclamation_mark', 'has_question_mark', 'average_da', 'DOW_ohe', 'subreddit_type_ohe', 'result1_ohe']

In [30]:
vect_asmb_3=VectorAssembler(inputCols=X_oot.columns,outputCol='features')
oot_testing_df=vect_asmb_3.transform(oot_df).select('features','score')
display(oot_testing_df)

features score List(0, 27, List(0, 2, 5, 6, 10, 11, 12, 14, 15, 18, 22, 26), List(1.0, 1.0, 1.0, 1.0, 1.0, 69.0, 50.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 1, 2, 5, 6, 10, 11, 12, 14, 15, 18, 22, 24), List(2.0, 1.0, 2.0, 1.0, 1.0, 1.0, 30.0, 73.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 14, 15, 18, 22, 24), List(1.0, 4.0, 1.0, 1.0, 1.0, 38.0, 62.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 5, 10, 11, 12, 15, 18, 22, 24), List(1.0, 5.0, 1.0, 1.0, 75.0, 63.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 List(0, 27, List(0, 1, 2, 6, 10, 11, 12, 15, 18, 23, 25), List(3.0, 1.0, 1.0, 1.0, 1.0, 24.0, 26.0, 93.46056782334385, 1.0, 1.0, 1.0)) 11 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 18, 22, 24), List(1.0, 6.0, 1.0, 1.0, 1.0, 28.0, 53.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 1, 2, 5, 10, 11, 12, 15, 18, 22, 24), List(59.0, 1.0, 7.0, 1.0, 1.0, 43.0, 38.0, 93.46056782334385, 1.0, 1.0, 1.0)) 196 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 18, 22, 24), List(1.0, 8.0, 1.0, 1.0, 1.0, 31.0, 34.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 List(0, 27, List(2, 4, 5, 6, 10, 11, 12, 15, 18, 22, 24), List(9.0, 1.0, 1.0, 1.0, 1.0, 46.0, 42.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 5, 10, 11, 12, 15, 18, 22, 24), List(1.0, 10.0, 1.0, 1.0, 34.0, 41.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 14, 15, 18, 22, 24), List(1.0, 12.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 30.0, 42.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 1, 2, 5, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(3.0, 1.0, 13.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 19.0, 42.0, 93.46056782334385, 1.0, 1.0, 1.0)) 2 List(0, 27, List(1, 2, 6, 8, 9, 10, 11, 12, 15, 18, 23, 24), List(1.0, 3.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 55.0, 41.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(1, 2, 4, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(1.0, 14.0, 1.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 65.0, 64.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(15.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 20.0, 48.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(16.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 36.0, 64.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(17.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 38.0, 66.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(18.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 37.0, 65.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(19.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 37.0, 65.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 1, 2, 4, 5, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(86.0, 1.0, 24.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 70.0, 125.0, 93.46056782334385, 1.0, 1.0, 1.0)) 361 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(26.0, 1.0, 1.0, 2.0, 0.5195839405059814, 0.8544194102287292, 24.0, 59.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(1.0, 1.0, 27.0, 1.0, 1.0, 2.0, 0.5195839405059814, 0.8544194102287292, 19.0, 30.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 13, 15, 18, 22, 24), List(28.0, 1.0, 1.0, 2.0, 0.5195839405059814, 0.8544194102287292, 58.0, 69.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 List(0, 27, List(0, 1, 2, 5, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(7.0, 1.0, 29.0, 1.0, 2.0, 0.5195839405059814, 0.8544194102287292, 80.0, 77.0, 93.46056782334385, 1.0, 1.0, 1.0)) 83 List(0, 27, List(1, 2, 6, 7, 8, 9, 10, 11, 

In [31]:
oot_pred_df_rf=model.transform(oot_testing_df)
display(oot_pred_df_rf)

features score prediction List(0, 27, List(0, 2, 5, 6, 10, 11, 12, 14, 15, 18, 22, 26), List(1.0, 1.0, 1.0, 1.0, 1.0, 69.0, 50.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.2989392499765862 List(0, 27, List(0, 1, 2, 5, 6, 10, 11, 12, 14, 15, 18, 22, 24), List(2.0, 1.0, 2.0, 1.0, 1.0, 1.0, 30.0, 73.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.727587514392809 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 14, 15, 18, 22, 24), List(1.0, 4.0, 1.0, 1.0, 1.0, 38.0, 62.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.9231077892535442 List(0, 27, List(1, 2, 5, 10, 11, 12, 15, 18, 22, 24), List(1.0, 5.0, 1.0, 1.0, 75.0, 63.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 12.438880680420402 List(0, 27, List(0, 1, 2, 6, 10, 11, 12, 15, 18, 23, 25), List(3.0, 1.0, 1.0, 1.0, 1.0, 24.0, 26.0, 93.46056782334385, 1.0, 1.0, 1.0)) 11 5.596834006257988 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 18, 22, 24), List(1.0, 6.0, 1.0, 1.0, 1.0, 28.0, 53.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.935849092818822 List(0, 27, List(0, 1, 2, 5, 10, 11, 12, 15, 18, 22, 24), List(59.0, 1.0, 7.0, 1.0, 1.0, 43.0, 38.0, 93.46056782334385, 1.0, 1.0, 1.0)) 196 134.477499179583 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 18, 22, 24), List(1.0, 8.0, 1.0, 1.0, 1.0, 31.0, 34.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 1.1042255267630168 List(0, 27, List(2, 4, 5, 6, 10, 11, 12, 15, 18, 22, 24), List(9.0, 1.0, 1.0, 1.0, 1.0, 46.0, 42.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.6991384765205239 List(0, 27, List(1, 2, 5, 10, 11, 12, 15, 18, 22, 24), List(1.0, 10.0, 1.0, 1.0, 34.0, 41.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 12.132823612758973 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 14, 15, 18, 22, 24), List(1.0, 12.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 30.0, 42.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.1448586848173732 List(0, 27, List(0, 1, 2, 5, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(3.0, 1.0, 13.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 19.0, 42.0, 93.46056782334385, 1.0, 1.0, 1.0)) 2 33.201902765998554 List(0, 27, List(1, 2, 6, 8, 9, 10, 11, 12, 15, 18, 23, 24), List(1.0, 3.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 55.0, 41.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 2.0088887835563107 List(0, 27, List(1, 2, 4, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(1.0, 14.0, 1.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 65.0, 64.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.2452627224115016 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(15.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 20.0, 48.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.682317512076392 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(16.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 36.0, 64.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.6555783368181389 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(17.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 38.0, 66.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.6608964404214148 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(18.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 37.0, 65.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.6555783368181389 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(19.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 37.0, 65.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.6555783368181389 List(0, 27, List(0, 1, 2, 4, 5, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(86.0, 1.0, 24.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 70.0, 125.0, 93.46056782334385, 1.0, 1.0, 1.0)) 361 161.81544684393282 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(26.0, 1.0, 1.0, 2.0, 0.5195839405059814, 0.8544194102287292, 24.0, 59.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.6542927414961394 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(1.0, 1.0, 27.0, 1.0, 1.0, 2.0, 0.5195839405059814, 0.8544194102287292, 19.0, 30.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.0028806

In [32]:
rmse_3=eval_1.evaluate(oot_pred_df_rf)
print('RMSE value of best model on OOT:',rmse_3)

RMSE value of best model on OOT: 20.42984373900492

In [33]:
r2_oot=eval_2.evaluate(oot_pred_df_rf)
print('R-square value of best model on OOT:', r2_oot)

R-square value of best model on OOT: 0.5624531677674804

In [34]:
prediction_oot=cv.transform(oot_testing_df)
display(prediction_oot)

features score prediction List(0, 27, List(0, 2, 5, 6, 10, 11, 12, 14, 15, 18, 22, 26), List(1.0, 1.0, 1.0, 1.0, 1.0, 69.0, 50.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.781459449830633 List(0, 27, List(0, 1, 2, 5, 6, 10, 11, 12, 14, 15, 18, 22, 24), List(2.0, 1.0, 2.0, 1.0, 1.0, 1.0, 30.0, 73.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 3.351179292820757 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 14, 15, 18, 22, 24), List(1.0, 4.0, 1.0, 1.0, 1.0, 38.0, 62.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.9931438574504691 List(0, 27, List(1, 2, 5, 10, 11, 12, 15, 18, 22, 24), List(1.0, 5.0, 1.0, 1.0, 75.0, 63.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 12.565957456974997 List(0, 27, List(0, 1, 2, 6, 10, 11, 12, 15, 18, 23, 25), List(3.0, 1.0, 1.0, 1.0, 1.0, 24.0, 26.0, 93.46056782334385, 1.0, 1.0, 1.0)) 11 4.108435548572342 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 18, 22, 24), List(1.0, 6.0, 1.0, 1.0, 1.0, 28.0, 53.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.02822392532322 List(0, 27, List(0, 1, 2, 5, 10, 11, 12, 15, 18, 22, 24), List(59.0, 1.0, 7.0, 1.0, 1.0, 43.0, 38.0, 93.46056782334385, 1.0, 1.0, 1.0)) 196 155.21408715653016 List(0, 27, List(1, 2, 5, 6, 10, 11, 12, 15, 18, 22, 24), List(1.0, 8.0, 1.0, 1.0, 1.0, 31.0, 34.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 0.9926980461298441 List(0, 27, List(2, 4, 5, 6, 10, 11, 12, 15, 18, 22, 24), List(9.0, 1.0, 1.0, 1.0, 1.0, 46.0, 42.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.0098843460444817 List(0, 27, List(1, 2, 5, 10, 11, 12, 15, 18, 22, 24), List(1.0, 10.0, 1.0, 1.0, 34.0, 41.0, 93.46056782334385, 1.0, 1.0, 1.0)) 1 12.112115772235828 List(0, 27, List(1, 2, 5, 6, 8, 9, 10, 11, 12, 14, 15, 18, 22, 24), List(1.0, 12.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 30.0, 42.0, 1.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.1211918363418327 List(0, 27, List(0, 1, 2, 5, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(3.0, 1.0, 13.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 19.0, 42.0, 93.46056782334385, 1.0, 1.0, 1.0)) 2 31.81414230533306 List(0, 27, List(1, 2, 6, 8, 9, 10, 11, 12, 15, 18, 23, 24), List(1.0, 3.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 55.0, 41.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.8168451105426857 List(0, 27, List(1, 2, 4, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(1.0, 14.0, 1.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 65.0, 64.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 1.7175119484288908 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(15.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 20.0, 48.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.5201818274553238 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(16.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 36.0, 64.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.5375609623253306 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(17.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 38.0, 66.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.5383934249670815 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(18.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 37.0, 65.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.5375609623253306 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(19.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 37.0, 65.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.5375609623253306 List(0, 27, List(0, 1, 2, 4, 5, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(86.0, 1.0, 24.0, 1.0, 1.0, 1.0, 0.269796758890152, 0.9629172682762146, 70.0, 125.0, 93.46056782334385, 1.0, 1.0, 1.0)) 361 154.8752526579096 List(0, 27, List(2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(26.0, 1.0, 1.0, 2.0, 0.5195839405059814, 0.8544194102287292, 24.0, 59.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.4826970073386869 List(0, 27, List(0, 1, 2, 5, 6, 8, 9, 10, 11, 12, 15, 18, 22, 24), List(1.0, 1.0, 27.0, 1.0, 1.0, 2.0, 0.5195839405059814, 0.8544194102287292, 19.0, 30.0, 93.46056782334385, 1.0, 1.0, 1.0)) 0 0.95471923

In [35]:
rmse_3=eval_1.evaluate(prediction_oot)
print('RMSE value of base random forest regression model on test:',rmse_3)


RMSE value of base random forest regression model on test: 20.73632014922789

In [36]:
r2_oot=eval_2.evaluate(prediction_oot)
print('R-square value of random forest regression model on test:', r2_oot)


R-square value of random forest regression model on test: 0.5492270646303394

In [37]:
model.featureImportances

Out[35]: SparseVector(27, {0: 0.677, 1: 0.0025, 2: 0.0187, 3: 0.0003, 4: 0.0024, 5: 0.0082, 6: 0.1892, 7: 0.0005, 8: 0.0083, 9: 0.012, 10: 0.0103, 11: 0.0168, 12: 0.0162, 13: 0.0028, 14: 0.0018, 15: 0.0082, 16: 0.0012, 17: 0.0017, 18: 0.0017, 19: 0.0016, 20: 0.0013, 21: 0.0033, 22: 0.0052, 23: 0.0048, 24: 0.0007, 25: 0.0028, 26: 0.0004})

In [38]:
feat=model.featureImportances
feat=feat.toArray()
feat=feat.tolist()
print(feat)

[0.6770320449990362, 0.002475355531922467, 0.018743436395179246, 0.0002601293531664598, 0.002422108830984211, 0.008242097856063902, 0.18922564924326152, 0.0004658942521247967, 0.008306853286392588, 0.0119705023126729, 0.010308252868137633, 0.016770523875244265, 0.016221848544468447, 0.002812846880232208, 0.0018020365656963582, 0.008197218662781098, 0.0012412214027417046, 0.0017063797975626993, 0.0017357506328789939, 0.0016377579606223738, 0.0013155113932981277, 0.0032807153382957703, 0.005162790366525278, 0.00478793899963851, 0.0007273874140256412, 0.002777409275370259, 0.0003703379616762544]

In [39]:
Col=X_train.columns
print(Col)

['num_comments', 'is_crosspostable_encoded', 'subreddit_hotness', 'author_cakeday_encoded', 'author_flair_text_color_encoded', 'brand_safe_encoded', 'no_follow_enc', 'over_18_enc', 'create_hour', 'created_hour_sin', 'created_hour_cos', 'length_title', 'url_length', 'has_exclamation_mark', 'has_question_mark', 'average_da', 'DOW_ohe', 'subreddit_type_ohe', 'result1_ohe']

In [40]:
from pyspark.sql.functions import lit
from pyspark.sql.functions import row_number
from pyspark.sql.window import Window
df=spark.createDataFrame(Col,schema="string")
df=df.withColumnRenamed("value","Features")
df=df.withColumn("Index",row_number().over(Window.orderBy(lit(1))))
display(df)

Features Index num_comments 1 is_crosspostable_encoded 2 subreddit_hotness 3 author_cakeday_encoded 4 author_flair_text_color_encoded 5 brand_safe_encoded 6 no_follow_enc 7 over_18_enc 8 create_hour 9 created_hour_sin 10 created_hour_cos 11 length_title 12 url_length 13 has_exclamation_mark 14 has_question_mark 15 average_da 16 DOW_ohe 17 subreddit_type_ohe 18 result1_ohe 19

In [41]:
df_2=spark.createDataFrame(feat,schema="float")
df_2=df_2.withColumnRenamed("value","Feature_importances")
df_2=df_2.withColumn("Index",row_number().over(Window.orderBy(lit(1))))
display(df_2)

Feature_importances Index 0.67703205 1 0.0024753555 2 0.018743437 3 2.6012937E-4 4 0.0024221088 5 0.008242098 6 0.18922564 7 4.6589426E-4 8 0.0083068535 9 0.011970502 10 0.010308253 11 0.016770523 12 0.01622185 13 0.0028128468 14 0.0018020365 15 0.008197219 16 0.0012412214 17 0.0017063798 18 0.0017357506 19 0.001637758 20 0.0013155114 21 0.0032807153 22 0.0051627904 23 0.004787939 24 7.2738744E-4 25 0.0027774093 26 3.7033795E-4 27

In [42]:
df_3=df.join(df_2,on="Index")
display(df_3)

Index Features Feature_importances 1 num_comments 0.67703205 2 is_crosspostable_encoded 0.0024753555 3 subreddit_hotness 0.018743437 4 author_cakeday_encoded 2.6012937E-4 5 author_flair_text_color_encoded 0.0024221088 6 brand_safe_encoded 0.008242098 7 no_follow_enc 0.18922564 8 over_18_enc 4.6589426E-4 9 create_hour 0.0083068535 10 created_hour_sin 0.011970502 11 created_hour_cos 0.010308253 12 length_title 0.016770523 13 url_length 0.01622185 14 has_exclamation_mark 0.0028128468 15 has_question_mark 0.0018020365 16 average_da 0.008197219 17 DOW_ohe 0.0012412214 18 subreddit_type_ohe 0.0017063798 19 result1_ohe 0.0017357506

In [43]:
df_3=df_3.drop("Index")

In [44]:
display(df_3)

Features Feature_importances num_comments 0.67703205 is_crosspostable_encoded 0.0024753555 subreddit_hotness 0.018743437 author_cakeday_encoded 2.6012937E-4 author_flair_text_color_encoded 0.0024221088 brand_safe_encoded 0.008242098 no_follow_enc 0.18922564 over_18_enc 4.6589426E-4 create_hour 0.0083068535 created_hour_sin 0.011970502 created_hour_cos 0.010308253 length_title 0.016770523 url_length 0.01622185 has_exclamation_mark 0.0028128468 has_question_mark 0.0018020365 average_da 0.008197219 DOW_ohe 0.0012412214 subreddit_type_ohe 0.0017063798 result1_ohe 0.0017357506

In [45]:
from pyspark.sql.functions import lit
from pyspark.sql.functions import row_number
from pyspark.sql.window import Window
r2_list=[0.564407,0.5908,0.4427]
rmse_list=[19.3647,18.8537,22.0045]

In [46]:
df=spark.createDataFrame(r2_list,schema="float")
df=df.withColumnRenamed("value","R2_values")
df=df.withColumn("Index",row_number().over(Window.orderBy(lit(1))))
display(df)

R2_values Index 0.564407 1 0.5908 2 0.4427 3

In [47]:
df_4=spark.createDataFrame(rmse_list,schema="float")
df_4=df_4.withColumnRenamed("value","RMSE_values")
df_4=df_4.withColumn("Index",row_number().over(Window.orderBy(lit(1))))
display(df_4)

RMSE_values Index 19.3647 1 18.8537 2 22.0045 3

In [48]:
mod=['GBTrees','Random_Forest','Linear_Regresion']
df_5=spark.createDataFrame(mod,schema="string")
df_5=df_5.withColumnRenamed("value","Models")
df_5=df_5.withColumn("Index",row_number().over(Window.orderBy(lit(1))))
display(df_5)

Models Index GBTrees 1 Random_Forest 2 Linear_Regresion 3

In [49]:
df_6=df.join(df_5,on='Index')
display(df_6)

Index R2_values Models 1 0.564407 GBTrees 2 0.5908 Random_Forest 3 0.4427 Linear_Regresion

In [50]:
df_7=df_4.join(df_5,on='Index')
display(df_7)

Index RMSE_values Models 1 19.3647 GBTrees 2 18.8537 Random_Forest 3 22.0045 Linear_Regresion